# Learning how to walk while cat-walking ~ demo app
Hello this is a demo for the SI16 API and website from XPUB. Trying to document everything so it is not OBSCURE. Feel free to improve anything!

The folder structure follows this scheme: 
- In the ```root``` folder there is the notebook (this file) that runs the Flask application. 
- The ```templates``` folder is the default one from Flask with the HTML templates. 
- In the ```notebooks``` folder there are the files with the basic functions and their documentation in the format of notebook. 
- In the ```projects``` folder there are the folders of the subgroup projects. We can put the files and materials of each project in there as well as the html pages etc. Each project should have also an ```documentation.md``` file with the info of the work. 
- In the ```static``` folder there are all the static files such as css stylesheets, fonts, images, javascript files, etc. They are organized in specific sub-folders so we dont get messy   
- In the ```contents``` folder there are all the markdown files with the text contents for the website. Description of the projects, about, colophon, manifesto, research etc. Each file contains the text and can include some metadata of our choice. Look at the about.md for an example 

## Import
Here we import all the modules we need for making the app working.

In [14]:
# to work with files in folder 
import os

# to create the Flask app
from flask import Flask, render_template, request, url_for, redirect, jsonify, abort

# to import text contents and metadata from markdown files
from flaskext.markdown import Markdown
import frontmatter

# to cast string arguments into the required types
from pydoc import locate

# to work with notebooks
#
# to import notebook files
import nbimporter
nbimporter.options['only_defs'] = False
import importlib

# to read and execute the content of notebooks
import nbformat
from nbconvert import HTMLExporter, MarkdownExporter
from nbconvert.preprocessors import ExecutePreprocessor

# not sure about this is in the nbconvert documentation
from traitlets.config import Config



## Functions
Here we define the functions for the logic of the backend and the API 

In [15]:
def filenames(folder):
    ''' Read all the functions in a folder '''
    names = []
    for entry in os.scandir(folder):
        # add to the list only proper files
        if entry.is_file(follow_symlinks=False):
            # remove the extension from the filename
            names.append(os.path.splitext(entry.name)[0])
    return names

In [16]:
# example: print the file inside the notebooks folder
print(filenames('./notebooks'))

['vernacular_map', 'text_file_to_blob', 'shout', 'reverse', 'cocktail_generator', 'blob_to_excerpts_list', 'mashup', 'repeat', 'highlight_map', 'individual_map', 'bridge', 'add_target_info', 'area_map', 'input-back-to-text', 'target_map', 'ghost_map', 'html_tag']


In [17]:
def dirnames(folder):
    ''' Return all the folders in a folder '''
    names = []
    for entry in os.scandir(folder):
        # add to the list only proper files
        if not entry.name.startswith('.') and entry.is_dir():
            # remove the extension from the filename
            names.append(entry.name)
    return names

In [18]:
print(dirnames('./projects'))

['etc', 'replace', 'map']


In [19]:
# not really sure about this file -> module -> function thing! 
# could someone help pls ? 
def get_function(name, folder):
    ''' Dynamic import a function from a folder '''
#     try: 
    file  = __import__(f'{folder}.{name}')
    module = getattr(file, name)
    function = getattr(module, name)
#     except AttributeError or ModuleNotFoundError:
#         file = importlib.import_module(f'{folder}.{name}')
#         function = getattr(file, name)
    return function

In [20]:
# example: try a couple of functions from the notebooks folder
rep = get_function('repeat', 'notebooks')
print(rep('Hello'))

sh = get_function('shout','notebooks')
print(sh('Salut'))

# sc = get_function('scream', 'notebooks')
# print(sc('Buenos dias'))

HelloHello
Saaaaaluuuuut


In [21]:
def get_function_info(function):
    ''' Extract info from a function '''
    name = function.__name__
    description = function.__doc__
    parameters = []
    output = ''

    # TODO: default values 
    
    # populate a list of tuple with patameter, type
    for param in function.__annotations__.keys():
        if param == 'return':
            output = function.__annotations__[param].__name__
        if param != 'return':
            parameters.append((param, function.__annotations__[param].__name__))
    
    return(name, description, parameters, output)

In [22]:
def print_info(function):
    ''' Print the info of a function nicely '''
    name, description, parameters, output = get_function_info(function)
    
    # very important feature
    from kaomoji.kaomoji import Kaomoji
    kao = Kaomoji()
    
    header = f'----------{kao.create()}'
    footer = '-' * len(header)
    
    print(header)
    print(name)
    print(description)
    print('Input:')
    for param, tp in parameters:
        print(f'  {param}, of type {tp}')
    print(f'Returns a {output}')
    print(footer)

In [23]:
print_info(rep)

----------＼(^ヮ☆)ノ
repeat
Repeat a string for a specified number of times
Input:
  text, of type str
  times, of type int
Returns a str
-----------------


In [24]:
# optionally you can pass a boolean argument to execute the notebook before the export
# but it is a slow process so by default is not active
# TODO: markdown export instead of HTML ? 
# TODO: extract images from base64
def get_notebook_contents(filename, execute = False):
    ''' Export notebook contents as HTML. '''
    with open(filename) as f:
        nb = nbformat.read(f, as_version=4)
        
        if execute:
            ep = ExecutePreprocessor(timeout=600, kernel_name='python3')
            ep.preprocess(nb, {'metadata':{'path':'notebooks/'}})
        
    html_exporter = HTMLExporter()    
    html_exporter.template_name = 'basic'    
    (body, resources) = html_exporter.from_notebook_node(nb)    
    
    return body
    
#     with open('executed_notebook.ipynb', 'w', encoding='utf-8') as f:
#         nbformat.write(nb, f)

In [25]:
get_notebook_contents('./notebooks/repeat.ipynb')

'<!DOCTYPE html>\n<html>\n<head><meta charset="utf-8" />\n<meta name="viewport" content="width=device-width, initial-scale=1.0">\n\n<title>Notebook</title><script src="https://cdnjs.cloudflare.com/ajax/libs/require.js/2.1.10/require.min.js"></script>\n\n\n\n\n<style type="text/css">\n    pre { line-height: 125%; }\ntd.linenos .normal { color: inherit; background-color: transparent; padding-left: 5px; padding-right: 5px; }\nspan.linenos { color: inherit; background-color: transparent; padding-left: 5px; padding-right: 5px; }\ntd.linenos .special { color: #000000; background-color: #ffffc0; padding-left: 5px; padding-right: 5px; }\nspan.linenos.special { color: #000000; background-color: #ffffc0; padding-left: 5px; padding-right: 5px; }\n.highlight .hll { background-color: var(--jp-cell-editor-active-background) }\n.highlight { background: var(--jp-cell-editor-background); color: var(--jp-mirror-editor-variable-color) }\n.highlight .c { color: var(--jp-mirror-editor-comment-color); font-

In [26]:
# EXPORT AS MARKDOWN
def get_notebook_md(filename, execute = False):
    ''' Export notebook contents as Markdown. '''
    with open(filename) as f:
        nb = nbformat.read(f, as_version=4)
        
        if execute:
            ep = ExecutePreprocessor(timeout=600, kernel_name='python3')
            ep.preprocess(nb, {'metadata':{'path':'notebooks/'}})
        
    md_exporter = MarkdownExporter()    
    
#     html_exporter.template_name = 'basic'    
    (body, resources) = md_exporter.from_notebook_node(nb)    
    
    return body
    
#     with open('executed_notebook.ipynb', 'w', encoding='utf-8') as f:
#         nbformat.write(nb, f)

In [28]:
print(get_notebook_md('./notebooks/repeat.ipynb'))

# Repeat
Repeat a string for a specified number of times


```python
def repeat(text: str, times: int = 2) -> str:
    """Repeat a string for a specified number of times"""
    return text * times
```

![ara repeating itself](https://www.dienst.nl/sub/upload/images/1/30019_550.jpg)

This function has many attractive qualities, but its ability to repeat human speech is one that makes it truly unique among other types of companion python functions and one that has ensured its popularity for generations. You are likely to find, though, that the function's talents for mimicry still pales in comparison to the fact that it is charming, engaging, and truly remarkable. Here is one of the most popular repeating function so that you can appreciate more about what it has to offer. It often says injuries to people and computers. 

## Examples

The function takes a string as a parameter, and by default it repeats it twice. 


```python
repeat('hello')
```




    'hellohello'



Eventually with a s

In [15]:
def get_contents(filename, directory = './contents'):
    ''' Return contents from a filename as frontmatter handler '''
    with open(f"{directory}/{filename}", "r") as f:
        content = frontmatter.load(f)
    return content

In [16]:
# example: print the contents of the about file
test_about = get_contents('about.md')

print(test_about['title'])
print(test_about['description'])
print()
print(test_about.content)

About
These are the info about SI16 - Learning how to walk while cat-walking

Dear friend and online scroller,
Beloved internet user, 
Dearest anonymous scroller binge watcher and human being IRL, 

![bibi](/soupboat/si16-app/static/img/bibi.jpg)

Do you like cats? Fond of Walking? Never heard of Python? (No. Not the snake) 
Great. 
You're very welcome to check out our Special Issue 16 on vernacular language processing: Learning How to Walk while Cat-walking. It is about  embracing vulnerability, sharing the clumsiness with little time and little technical knowledge in the form of a toolkit and encourage others to cat-walk with us.

Our toolkit wants to mess around with language that creates relations of power in its structuring information, in its grammar rules, in its standard taxonomies, categories and tags, in its organizing data and shaping knowledge, in its legitimizing hierarchies in a dialogue between two or more people... |__(we could use the etc tool here heheh)__| in order t

## Flask App

In [ ]:
# create flask application
app = Flask(__name__)
Markdown(app)

base_url = "si16-app"
notebooks = "notebooks"
projects = "projects"


# For specific pages we can build and link dedicated templates


# Homepage
@app.route(f"/{base_url}/")
def home_page():
    return render_template("home.html")


# About Page
@app.route(f"/{base_url}/about/")
def about_page():
    about = get_contents('about.md')
    return render_template("about.html", title = about['title'], description = about['description'], contents=about.content)

# Terms of Service page
@app.route(f"/{base_url}/tos/")
def tos_page():
    about = get_contents('tos.md')
    return render_template("tos.html", title = about['title'], description = about['description'], contents=about.content)

# For generic pages we can include a common template and change only the contents
@app.route(f"/{base_url}/<slug>/")
def dynamic_page(slug = None):
    try:
        page = get_contents(f"{slug}.md").to_dict()
        # page is a dictionary that contains: 
        # - all the attributes in the markdown file (ex: title, description, soup, etc)
        # - the content of the md in the property 'content'
        # in this way we can access those frontmatter attributes in jinja simply using the variables title, description, soup, etc
        return render_template("page.html", **page)
    except FileNotFoundError:
        # TODO: a proper not found page
        return render_template('404.html')



# List of projects
@app.route(f"/{base_url}/projects/")
def projects_list():
    # get a list of the functions from the notebooks folder
    projects = dirnames("./projects")

    # generate a link to each function
    return render_template("projects.html", projects=projects)


# Single project
@app.route(f"/{base_url}/projects/<project>/")
def p_info(project = None):
    try:
        page = get_contents("documentation.md", f"./{projects}/{project}").to_dict()
        return render_template("project.html", **page)
    except FileNotFoundError:
        return render_template('404.html')
    

    
# List of functions
@app.route(f"/{base_url}/functions/")
def functions_list():
    # get a list of the functions from the notebooks folder
    functions = filenames("./notebooks")

    # generate a link to each function
    return render_template("functions.html", functions=functions)


# Single Function page
@app.route(f"/{base_url}/functions/<function>/")
def f_info(function=None):
    if function in filenames(f"./{notebooks}"):
        fx = get_function(function, notebooks)
        name, description, parameters, output = get_function_info(fx)

        # executing a notebook takes a lot of time mmm should we just send them without the results of the examples? or save it executed?
        documentation = get_notebook_contents(f"./{notebooks}/{function}.ipynb")

        return render_template("function.html", name=name, description=description, parameters=parameters, output=output, documentation=documentation)

    # TODO: meaningful error code return
    else:
        return render_template('404.html')

    
    
# Function API page

@app.route(f"/{base_url}/api/<function>/")
def f_api(function=None):
    if function in filenames(f"./{notebooks}"):

        fx = get_function(function, notebooks)
        name, description, parameters, output = get_function_info(fx)

        query_params = []
        for param, tp in parameters:
            a = request.args.get(param)
            # cast the type of the argument to the type that the function requires
            tp = locate(tp)
            a = tp(a)
            query_params.append(a)
        return fx(*query_params)

    # TODO: meaningful error code return
    return "mmmm there is no function with this name sorry"





# Error handlers!
@app.errorhandler(400)
def error_400(e):
    # bad request or invalid url
    return render_template('400.html'), 400

@app.errorhandler(403)
def error_403(e):
    # forbidden (for invalid key) for evemt mode when it's not the 17th of the month
    return render_template('403.html'), 403

@app.errorhandler(404)
def error_404(e):
    # page not found
    return render_template('404.html'), 404

@app.errorhandler(500)
def error_500(e):
    # internal server error
    return render_template('500.html'), 500

@app.errorhandler(502)
def error_502(e):
    # bad gateaway
    return render_template('502.html'), 502

@app.errorhandler(503)
def error_503(e):
    # service temporarily unavailable, for secret breaks
    return render_template('503.html'), 503

@app.errorhandler(504)
def error_503(e):
    # ???????? gateway timeout shall we put it?????
    return render_template('504.html'), 504
app.run(port="3130")


 * Serving Flask app '__main__' (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:3130/ (Press CTRL+C to quit)
127.0.0.1 - - [08/Dec/2021 19:21:38] "GET /si16-app/ HTTP/1.0" 200 -
127.0.0.1 - - [08/Dec/2021 19:21:40] "GET /si16-app/projects/ HTTP/1.0" 200 -
127.0.0.1 - - [08/Dec/2021 19:21:43] "GET /si16-app/functions/ HTTP/1.0" 200 -
[2021-12-08 19:21:47,463] ERROR in app: Exception on /si16-app/functions/area_map/ [GET]
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/flask/app.py", line 2073, in wsgi_app
    response = self.full_dispatch_request()
  File "/usr/local/lib/python3.7/dist-packages/flask/app.py", line 1518, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "/usr/local/lib/python3.7/dist-packages/flask/app.py", line 1516, in full_dispatch_request
    rv = self.dispatch_request()
  File "/usr/local/lib/python3.7/dist-packages/flask/app.py", line 1502, in dispatch_request
    return self.ensure_sync(self.view_functions[rule.endpoint])(**req.view_args)
  File "/tmp/ipyker

*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*
*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*
*                             *
*   CATWALKING WITH ALCOHOL   *
*                             *
*    2021-12-08   21:06:28    *
*                             *
*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*
*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*



2 oz          RUM

150 ml        TONIC WATER

1 oz          LEMON JUICE

0.5 oz        MAPLE SIRUP

1 SLICE       CUCUMBER

1             UMBRELLA


*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*

EXTRA: SALTED CORN

*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*



               ___, 
              '._.'\ 
           _____/'-.\ 
          |    / | 
          |~~~/~~| 
          \ ()   / 
           '.__.' 
             || 
            _||_ 
           `----` 


THANKS FOR COMING TO OUR LAUNCH!

  (*(*(*(*(*.(*.*).*)*)*)*)*)*)


*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*
*=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*







[2021-12-08 20:06:33,187] ERROR in app: Exception on /si16-app/functions/cocktail_generator/ [GET]
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/flask/app.py", line 2073, in wsgi_app
    response = self.full_dispatch_request()
  File "/usr/local/lib/python3.7/dist-packages/flask/app.py", line 1518, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "/usr/local/lib/python3.7/dist-packages/flask/app.py", line 1516, in full_dispatch_request
    rv = self.dispatch_request()
  File "/usr/local/lib/python3.7/dist-packages/flask/app.py", line 1502, in dispatch_request
    return self.ensure_sync(self.view_functions[rule.endpoint])(**req.view_args)
  File "/tmp/ipykernel_9986/665664178.py", line 76, in f_info
    fx = get_function(function, notebooks)
  File "/tmp/ipykernel_9986/867254570.py", line 7, in get_function
    module = getattr(file, name)
AttributeError: module 'notebooks' has no attribute 'cocktail_generator'
127.0.0.1 - - [08